In [1]:
from __future__ import print_function
import chainer
import chainer.functions as F
import chainer.links as L
import chainerrl
import numpy as np
import gym
from gym import wrappers
import logging

In [2]:
from tqdm import tqdm

In [3]:
def phi(obs):
    return obs.astype(np.float32)

In [4]:
class A3CLSTMSoftmax(chainer.Chain, chainerrl.agents.a3c.A3CModel, chainerrl.recurrent.RecurrentChainMixin):
    def __init__(self):
        super(A3CLSTMSoftmax, self).__init__()
        with self.init_scope():
            self.conv1 = L.Convolution2D(3, 16, (11, 9), 1, 0)
            self.conv2 = L.Convolution2D(16, 32, (11, 9), 1, 0)
            self.conv3 = L.Convolution2D(32, 64, (10, 9), 1, 0)
            self.l4p = L.LSTM(14976, 1024) # ポリシーネットワーク
            self.l4v = L.LSTM(14976, 1024) # バリューネットワーク
            self.l5p = L.Linear(1024, 1024)
            self.l5v = L.Linear(1024, 1024)
            self.pi = chainerrl.policies.SoftmaxPolicy(L.Linear(1024, 6))
            self.v = L.Linear(1024, 1)
            
    def pi_and_v(self, state):
        state = np.asarray(state.transpose(0, 3, 1, 2), dtype=np.float32)
        h1 = F.max_pooling_2d(F.relu(self.conv1(state)), ksize=2, stride=2)
        h2 = F.max_pooling_2d(F.relu(self.conv2(h1)), ksize=2, stride=2) 
        h3 = F.max_pooling_2d(F.relu(self.conv3(h2)), ksize=2, stride=2)
        h4p = self.l4p(h3)
        h4v = self.l4v(h3)
        h5p = F.relu(self.l5p(h4p))
        h5v = F.relu(self.l5v(h4v))
        pout = self.pi(h5p) # ポリシーネットワークの出力
        vout = self.v(h5v) # バリューネットワークの出力
        return pout, vout

In [5]:
def make_env(process_idx, test=False):
    env = gym.make('SpaceInvaders-v0')
    process_seed = int(process_seeds[process_idx])
    if not test:
        chainerrl.misc.env_modifiers.make_reward_filtered(env, lambda x: x*0.01)
    if process_idx == 0 and not test:
        env = gym.wrappers.Monitor(env, outdir)
    env_seed = 2 ** 32 - 1 - process_seed if test else process_seed
    env.seed(env_seed)
    return env

In [6]:
num_episodes = 100000

In [7]:
model = A3CLSTMSoftmax()
optimizer = chainerrl.optimizers.rmsprop_async.RMSpropAsync(lr=0.001, eps=0.1, alpha=0.99)
optimizer.setup(model)

In [9]:
agent = chainerrl.agents.a3c.A3C(
    model, 
    optimizer, 
    t_max = 8,
    gamma = 0.995,
    beta = 0.1,
    phi = phi,
)

In [10]:
gym.logger.set_level(0)
logging.basicConfig(level=logging.DEBUG)

In [13]:
n_process = 3
outdir = 'result'
chainerrl.misc.set_random_seed(0)
process_seeds = np.arange(n_process)

In [ ]:
chainerrl.experiments.train_agent_async(
    agent = agent,
    outdir = outdir,
    processes = n_process,
    make_env = make_env,
    profile = True,
    steps = 1000000,
    eval_interval = None,
    max_episode_len = num_episodes,
    logger = gym.logger
)

INFO: Making new env: SpaceInvaders-v0
INFO: Making new env: SpaceInvaders-v0
INFO: Making new env: SpaceInvaders-v0
INFO: Creating monitor directory result
INFO: Starting new video recorder writing to /home/yashima/ML/RL/chainer_book/A3C/result/openaigym.video.0.25760.video000000.mp4
DEBUG: Capturing video frame: path=/home/yashima/ML/RL/chainer_book/A3C/result/openaigym.video.0.25760.video000000.mp4
DEBUG: Starting ffmpeg with "ffmpeg -nostats -loglevel error -y -r 30 -f rawvideo -s:v 160x210 -pix_fmt rgb24 -i - -vf scale=trunc(iw/2)*2:trunc(ih/2)*2 -vcodec libx264 -pix_fmt yuv420p /home/yashima/ML/RL/chainer_book/A3C/result/openaigym.video.0.25760.video000000.mp4"


DEBUG:chainerrl.agents.a3c:t:1 r:0 a:4 pout:SoftmaxDistribution(beta=1.0, min_prob=0.0) logits:[[-0.60634923  0.13875708  0.2586704   0.20290095  0.21846941 -0.03822245]] probs:[[0.08493027 0.17891966 0.20171386 0.19077232 0.1937656  0.14989834]] entropy:[1.758759]


DEBUG: Capturing video frame: path=/home/yashima/ML/RL/chainer_book/A3C/result/openaigym.video.0.25760.video000000.mp4


DEBUG:chainerrl.agents.a3c:t:2 r:0.0 a:3 pout:SoftmaxDistribution(beta=1.0, min_prob=0.0) logits:[[-0.7547961   0.16335626  0.22208175  0.29930896  0.2036087  -0.14062813]] probs:[[0.07415171 0.1857247  0.1969581  0.21277136 0.19335307 0.13704112]] entropy:[1.7449545]


DEBUG: Capturing video frame: path=/home/yashima/ML/RL/chainer_book/A3C/result/openaigym.video.0.25760.video000000.mp4


...

DEBUG:chainerrl.agents.a3c:t:19326 r:0.0 a:4 pout:SoftmaxDistribution(beta=1.0, min_prob=0.0) logits:[[-0.0908429  -0.02117709 -0.04723999 -0.02257232 -0.05711843 -0.04209162]] probs:[[0.15944815 0.1709523  0.16655436 0.17071396 0.16491716 0.16741405]] entropy:[1.7914864]


DEBUG: Capturing video frame: path=/home/yashima/ML/RL/chainer_book/A3C/result/openaigym.video.0.25760.video000027.mp4


DEBUG:chainerrl.agents.a3c:t:19327 r:0.0 a:3 pout:SoftmaxDistribution(beta=1.0, min_prob=0.0) logits:[[-0.09130958 -0.021124   -0.04760187 -0.02251048 -0.05668168 -0.04248112]] probs:[[0.159391   0.17097987 0.16651212 0.17074299 0.16500705 0.16736695]] entropy:[1.7914835]


DEBUG: Capturing video frame: path=/home/yashima/ML/RL/chainer_book/A3C/result/openaigym.video.0.25760.video000027.mp4


DEBUG:chainerrl.agents.a3c:pi_loss:[-1.0878015] v_loss:[[0.00229733]]
